In [ ]:
%pip install gradio gensim sentence_transformers torch torchvision torchaudio -f https://download.pytorch.org/whl/cu111/torch_stable.html

In [ ]:
import pandas as pd
import networkx as nx
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel
from textblob import TextBlob
from nltk.sentiment.vader import SentimentIntensityAnalyzer
import nltk
from nltk import pos_tag
from nltk.tokenize import word_tokenize
from gensim.models import Word2Vec
import spacy
from sentence_transformers import SentenceTransformer, util
import numpy as np
import torch
import gradio as gr
import os
import math
from datetime import datetime

# Use GPU
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load a BERT model
bert_model = SentenceTransformer('paraphrase-MiniLM-L6-v2', device=device)

# Download NLTK resources (if not already downloaded)
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')
nltk.download('vader_lexicon')

# Load Spacy model for Named Entity Recognition (NER)
nlp = spacy.load("en_core_web_sm")

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package vader_lexicon to /root/nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!


In [ ]:
# Load Yelp dataset
yelp_data = pd.read_csv('restaurants.csv')

# Filter out relevant information (e.g., restaurant name, rating, location, categories, hours)
restaurants = yelp_data[['name', 'stars', 'city', 'categories', 'hours']]

comfort_food_terms = [
    "Home cooking",
    "Soul food",
    "Indulgent food",
    "Feel-good food",
    "Nostalgia food",
    "Emotional food",
    "Guilty pleasure",
    "Indulgence",
    "Treat",
    "Culinary hug",
    "Soul-soothing food",
    "Heart-warming food",
]

exciting_food_terms = [
    "Adventurous food",
    "Exotic food",
    "Culinary adventure",
    "Sensual food",
    "Tantalizing food",
    "Mouthwatering food",
    "Delectable food",
    "Irresistible food",
    "Tempting food",
    "Gastronomical delight",
]

In [ ]:
# Create a TF-IDF vectorizer to convert restaurant categories into numerical features
tfidf_vectorizer = TfidfVectorizer(stop_words='english', lowercase=True)
tfidf_matrix = tfidf_vectorizer.fit_transform(restaurants['categories']+", "+restaurants['city'].fillna(''))

# Train Word2Vec model on restaurant names
restaurant_names = [word_tokenize(restaurant['categories'].lower()+restaurant['city'].lower()) for _, restaurant in restaurants.iterrows()]
word2vec_model = Word2Vec(sentences=restaurant_names, vector_size=100, window=5, min_count=1, workers=4)

if os.path.isfile("./bert_embeddings.npy"):
    restaurant_embeddings = np.load('bert_embeddings.npy')
else:
    # Precompute restaurant embeddings on the chosen device for both categories and cities
    restaurant_embeddings = [bert_model.encode((restaurant['categories'].lower() + restaurant['city'].lower()), convert_to_tensor=True).detach().cpu().numpy()
                            for _, restaurant in restaurants.iterrows()]
    np.save('bert_embeddings.npy', np.array(restaurant_embeddings))
    restaurant_embeddings = np.load('bert_embeddings.npy')


# Build a knowledge graph
knowledge_graph = nx.Graph()

# Add restaurant nodes with attributes
for _, restaurant in restaurants.iterrows():
    knowledge_graph.add_node(
        restaurant['name'],
        stars=restaurant['stars'],
        city=restaurant['city'],
        categories=restaurant['categories'],
        hours=restaurant['hours']
    )

# Function to extract named entities from user input using Spacy NER
def extract_named_entities(user_input):
    doc = nlp(user_input)
    named_entities = [(ent.text, ent.label_) for ent in doc.ents]
    return named_entities

# Function to perform sentiment analysis using VADER
def analyze_sentiment_vader(text):
    sid = SentimentIntensityAnalyzer()
    compound_score = sid.polarity_scores(text)['compound']
    return compound_score

In [ ]:
# # Function to get restaurant recommendations based on graph similarity
# def get_graph_recommendations(user_nouns):
#     # Use graph-based similarity to get similar restaurants from the knowledge graph
#     # You can choose a graph similarity algorithm based on your requirements
#     # For example, you can use Jaccard similarity or node2vec embeddings
#     # For simplicity, let's use Jaccard similarity here
#     user_nouns_set = set(user_nouns)
#     graph_recommendations = set()

#     # print(user_nouns_set)
#     for restaurant in knowledge_graph.nodes():
#         restaurant_nouns = set(pos_tag(word_tokenize(restaurant)))
#         jaccard_similarity = len(user_nouns_set.intersection(restaurant_nouns)) / len(user_nouns_set.union(restaurant_nouns))

#         # print(restaurant, restaurant_nouns, jaccard_similarity)
#         # If Jaccard similarity is above a threshold, consider it a recommendation
#         if jaccard_similarity > 0.1:  # You can adjust the threshold
#             graph_recommendations.add(restaurant)

#     # print(graph_recommendations)
#     return graph_recommendations

# Function to get restaurant recommendations based on Word Overlap
def get_overlap_recommendations(user_input, num_recommendations):
    overlap_scores = pd.DataFrame()
    overlap_scores['combined_text'] = (restaurants['name'] + ", " + restaurants['categories'] + ", " + restaurants['city']).str.lower()
    overlap_scores['overlap_score'] = overlap_scores['combined_text'].apply(lambda x: sum(word in user_input.lower() for word in x.replace(',', '').split()))
    sorted_overlap_scores = overlap_scores.sort_values(by='overlap_score', ascending=False)
    top_recommendations_indices = [idx for idx, _ in sorted_overlap_scores.head(num_recommendations).iterrows()]
    return top_recommendations_indices


# Function to get restaurant recommendations based on Word Embeddings similarity
def get_embedding_recommendations(user_input, num_recommendations):
    tokens = word_tokenize(user_input.lower())
    embedding_similarities = {}

    for i, restaurant in restaurants.iterrows():
        restaurant_tokens = word_tokenize(restaurant['categories'].lower() + restaurant['city'].lower())
        similarity = word2vec_model.wv.n_similarity(tokens, restaurant_tokens)
        embedding_similarities[i] = similarity

    # Sort the dictionary by similarity scores and get top recommendations
    sorted_similarities = sorted(embedding_similarities.items(), key=lambda item: item[1], reverse=True)
    top_recommendations_indices = [idx for idx, _ in sorted_similarities[:num_recommendations]]

    return top_recommendations_indices

# Function to get restaurant recommendations based on BERT embeddings similarity
def get_bert_recommendations(user_input, num_recommendations):
    user_embedding = bert_model.encode(user_input.lower(), convert_to_tensor=True).detach().cpu().numpy()
    # user_embedding = np.mean(bert_model.encode(user_input.lower(), convert_to_tensor=True).detach().cpu().numpy(), axis=0)

    bert_similarities = {}

    for i, restaurant in restaurants.iterrows():
        restaurant_embedding = restaurant_embeddings[i]
        # print(restaurant_embedding, user_embedding)
        # similarity = np.dot(user_embedding, restaurant_embedding) / (np.linalg.norm(user_embedding) * np.linalg.norm(restaurant_embedding))
        similarity = util.cos_sim(user_embedding, restaurant_embedding)
        bert_similarities[i] = similarity
        # print(i, similarity)

    # Sort the dictionary by similarity scores and get top recommendations
    sorted_similarities = sorted(bert_similarities.items(), key=lambda item: item[1], reverse=True)
    top_recommendations_indices = [idx for idx, _ in sorted_similarities[:num_recommendations]]

    return top_recommendations_indices

In [ ]:
# Function to recommend restaurants based on user input, sentiment, availability, and knowledge graph
def recommend_restaurants(user_input, num_recommendations=5, sentiment_recursive_break=False):

    sr = pd.DataFrame()

    # Tokenize and perform POS tagging on the user input
    tokens = word_tokenize(user_input)
    pos_tags = pos_tag(tokens)

    # Extract nouns and locations from POS tags
    user_nouns = [word for word, pos in pos_tags if pos.startswith('N') or pos.startswith('J')]
    user_locations = [word.lower().strip() for word, pos in pos_tags if pos.startswith('NNP')]  # Assume proper nouns are locations
    # print(user_input)

    # Extract named entities from user input
    named_entities = extract_named_entities(user_input)
    # print("Named Entities:", named_entities)

    # Transform user input into a TF-IDF vector
    user_tfidf = tfidf_vectorizer.transform([user_input])

    # Compute the cosine similarity between the user input and restaurant categories
    cosine_similarities = linear_kernel(user_tfidf, tfidf_matrix).flatten()

    # Get recommended restaurants from simple word overlap
    overlap_recommendations = get_overlap_recommendations(user_input, num_recommendations)

    # Get indices of restaurants with the highest similarity scores using TF-IDF
    tfidf_recommendations = cosine_similarities.argsort()[:-num_recommendations-1:-1]

    # Get recommendations using Word Embeddings
    embedding_similarities = get_embedding_recommendations(user_input, num_recommendations)

    # Get recommendations using BERT
    bert_recommendations_indices = get_bert_recommendations(user_input, num_recommendations)

    # Combine recommendations from both approaches
    combined_recommendations = set(overlap_recommendations) | set(tfidf_recommendations) | set(embedding_similarities) |set(bert_recommendations_indices)
    combined_recommendations = set(embedding_similarities)
    # print("TFIDF:", tfidf_recommendations)
    # print("overlap:", overlap_recommendations)
    # print("w2v:", embedding_similarities)
    # print("BERT:", bert_recommendations_indices)

    # Get details of recommended restaurants
    recommended_restaurants = restaurants.iloc[list(combined_recommendations)]

    # print("rec res:", combined_recommendations)

    # Refine recommendations based on extracted information, location, and named entities
    for _, restaurant in recommended_restaurants.iterrows():
        # if any(category in restaurant['categories'] for category in user_nouns) and any(location in restaurant['city'] for location in user_locations):
        # if any(location in restaurant['city'].lower().strip() for location in user_locations):
            print(f"Recommendation: {restaurant['name'], restaurant['city'], restaurant['categories'], restaurant['stars']} ")

    if not sentiment_recursive_break:
      # Perform sentiment analysis using VADER
      sentiment_score = analyze_sentiment_vader(user_input)

      if sentiment_score < -0.2:
        print("Considering your negative sentiment, you might prefer comforting places.")
        sr = recommend_restaurants(user_input=user_input + ", " + ", ".join(comfort_food_terms), num_recommendations=num_recommendations, sentiment_recursive_break=True)
        # comforting_places = restaurants[restaurants['categories'].str.contains('comfort food', case=False, na=False)]
        # print("Comforting food places suggestions:")
        # print(comforting_places[['name', 'stars', 'city', 'categories']])
      elif sentiment_score > 0.2:
        print("Considering your positive sentiment, you might prefer something exciting.")
        sr = recommend_restaurants(user_input=user_input + ", " + ", ".join(exciting_food_terms), num_recommendations=num_recommendations, sentiment_recursive_break=True)
        # exciting_places = restaurants[restaurants['categories'].str.contains('nightlife|arts & entertainment|restaurants', case=False, na=False)]
        # print("Exciting food places suggestions:")
        # print(exciting_places[['name', 'stars', 'city', 'categories']])
      else:
        print("neutral sentiment")

    # Rank the restaurants based on ratings in descending order
    ranked_restaurants = recommended_restaurants.sort_values(by='stars', ascending=False).head(num_recommendations)

    # return recommended restaurants for evaluation
    return ranked_restaurants

In [ ]:
# Example prompt
user_prompt = input("Enter your restaurant preference (e.g., I want Chinese in Brooklyn): ")

# Get recommendations based on the user's input, sentiment, availability, and knowledge graph
recommend_restaurants(user_prompt)

In [ ]:
def evaluate_recommendations(predicted_df, filtered_df, k):
    """
    Evaluate predicted restaurant recommendations against the ground truth using precision@k, recall@k, and F1@k.

    Parameters:
    - predicted_df (pd.DataFrame): DataFrame with predicted restaurant recommendations.
    - filtered_df (pd.DataFrame): DataFrame with ground truth or actual relevant restaurants.
    - k (int): Value of k for top-k recommendations.

    Returns:
    - precision_at_k (float): Precision@k.
    - recall_at_k (float): Recall@k.
    - f1_at_k (float): F1@k.
    """

    # Extract the top-k predicted restaurants
    top_k_predicted = predicted_df.head(k)

    # Evaluate precision@k, recall@k, and F1@k
    intersection = pd.merge(top_k_predicted, filtered_df, on=['name', 'stars', 'city', 'categories', 'hours'], how='inner')

    precision_at_k = len(intersection) / k
    recall_at_k = len(intersection) / len(filtered_df)
    f1_at_k = 2 * (precision_at_k * recall_at_k) / (precision_at_k + recall_at_k) if (precision_at_k + recall_at_k) > 0 else 0

    return precision_at_k, recall_at_k, f1_at_k

In [ ]:
cajun_in_neworleans = restaurants[
    (restaurants['city'] == 'New Orleans') &
    (restaurants['categories'].str.contains('cajun', case=False))
]
steakhouses_in_indiana = restaurants[
    (restaurants['city'] == 'Indianapolis') &
    (restaurants['categories'].str.contains('steakhouse', case=False))
]
chinese_in_philadelphia = restaurants[
    (restaurants['city'] == 'Philadelphia') &
    (restaurants['categories'].str.contains('chinese', case=False))
]
seafood_in_tampa = restaurants[
    (restaurants['city'] == 'Tampa') &
    (restaurants['categories'].str.contains('seafood', case=False))
]
italian_in_stlouis = restaurants[
    (restaurants['city'] == 'Saint Louis') &
    (restaurants['categories'].str.contains('italian', case=False))
]

In [ ]:
cino = recommend_restaurants(input())

In [ ]:
print(evaluate_recommendations(cino, cajun_in_neworleans, 1))
print(evaluate_recommendations(cino, cajun_in_neworleans, 5))
print(evaluate_recommendations(cino, cajun_in_neworleans, 10))

In [ ]:
sit = recommend_restaurants(input())

In [ ]:
print(evaluate_recommendations(sit, seafood_in_tampa, 1))
print(evaluate_recommendations(sit, seafood_in_tampa, 5))
print(evaluate_recommendations(sit, seafood_in_tampa, 10))

In [ ]:
sii = recommend_restaurants(input())

In [ ]:
print(evaluate_recommendations(sii, steakhouses_in_indiana, 1))
print(evaluate_recommendations(sii, steakhouses_in_indiana, 5))
print(evaluate_recommendations(sii, steakhouses_in_indiana, 10))

In [ ]:
iisl = recommend_restaurants(input())

In [ ]:
print(evaluate_recommendations(iisl, italian_in_stlouis, 1))
print(evaluate_recommendations(iisl, italian_in_stlouis, 5))
print(evaluate_recommendations(iisl, italian_in_stlouis, 10))

In [ ]:
# rr = recommend_restaurants(prompt, number_of_recommendations = 5)

demo = gr.Interface(fn=recommend_restaurants, inputs=["text", gr.Number(value=10, precision=0, minimum=1)], outputs="dataframe")

if __name__ == "__main__":
    demo.launch(show_api=False, debug=True)

Setting queue=True in a Colab notebook requires sharing enabled. Setting `share=True` (you can turn this off by setting `share=False` in `launch()` explicitly).

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
Running on public URL: https://4a62505eb450484ce0.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


Recommendation: ("Charlie Gitto's On the Hill", 'St. Louis', 'Restaurants, Italian', 4.5) 
Recommendation: ("Pietro's", 'St. Louis', 'Italian, Restaurants', 4.0) 
Recommendation: ('Cluster Busters', 'St. Louis', 'Italian, Restaurants, Seafood', 4.0) 
Recommendation: ('Cibare Italian Kitchen', 'St. Louis', 'Restaurants, Italian', 4.0) 
Recommendation: ('Toscana Pizza, Pasta & More', 'St. Petersburg', 'Italian, Restaurants, Pizza', 4.0) 
Recommendation: ("Del Pietro's", 'St. Louis', 'Italian, Restaurants', 4.0) 
Recommendation: ("Sophia's Cucina + Enoteca", 'St. Petersburg', 'Italian, Restaurants', 4.0) 
Recommendation: ("Moscato's Bella Cucina", 'St. Petersburg', 'Italian, Restaurants', 3.5) 
Recommendation: ('Bici Trattoria', 'St. Petersburg', 'Italian, Restaurants', 4.0) 
Recommendation: ('Goodcents Deli Fresh Subs', 'St. Louis', 'Restaurants, Sandwiches', 4.0) 
neutral sentiment


In [ ]:
# import pandas as pd
# import networkx as nx
# from sklearn.feature_extraction.text import TfidfVectorizer
# from sklearn.metrics.pairwise import linear_kernel
# import nltk
# from nltk import pos_tag
# from nltk.tokenize import word_tokenize
# from datetime import datetime

# # Download NLTK resources (if not already downloaded)
# nltk.download('punkt')
# nltk.download('averaged_perceptron_tagger')

# # Load Yelp dataset (replace 'yelp_dataset.csv' with your actual dataset file)
# yelp_data = pd.read_csv('yelp_dataset.csv')

# # Load existing knowledge graph (replace 'knowledge_graph.gexf' with your actual graph file)
# knowledge_graph = nx.read_gexf('knowledge_graph.gexf')

# # Filter out relevant information (e.g., restaurant name, rating, location, categories, hours)
# restaurants = yelp_data[['name', 'stars', 'city', 'categories', 'hours']]

# # Create a TF-IDF vectorizer to convert restaurant categories into numerical features
# tfidf_vectorizer = TfidfVectorizer(stop_words='english', lowercase=True)
# tfidf_matrix = tfidf_vectorizer.fit_transform(restaurants['categories'].fillna(''))

# # Function to check if a restaurant is open at the current time
# def is_restaurant_open(hours, current_time):
#     for day, hours_range in hours.items():
#         start_time, end_time = hours_range.split('-')
#         if start_time <= current_time <= end_time:
#             return True
#     return False

# # Function to get similar foods from the knowledge graph
# def get_similar_foods(category, knowledge_graph):
#     similar_foods = set()

#     if category in knowledge_graph.nodes:
#         neighbors = list(knowledge_graph.neighbors(category))
#         similar_foods.update(neighbors)

#     return similar_foods

# # Function to recommend restaurants based on content-based filtering and availability
# def recommend_restaurants(user_input, num_recommendations=5):
#     # Tokenize and perform POS tagging on the user input
#     tokens = word_tokenize(user_input)
#     pos_tags = pos_tag(tokens)

#     # Extract nouns and locations from POS tags
#     user_nouns = [word for word, pos in pos_tags if pos.startswith('N') or pos.startswith('J')]
#     user_locations = [word for word, pos in pos_tags if pos.startswith('NNP')]  # Assume proper nouns are locations

#     # Filter restaurants based on the user's location
#     location_filtered_restaurants = restaurants[restaurants['city'].isin(user_locations)]

#     # Transform user input into a TF-IDF vector
#     user_tfidf = tfidf_vectorizer.transform([user_input])

#     # Compute the cosine similarity between the user input and restaurant categories
#     cosine_similarities = linear_kernel(user_tfidf, tfidf_matrix).flatten()

#     # Get indices of restaurants with highest similarity scores
#     restaurant_indices = cosine_similarities.argsort()[:-num_recommendations-1:-1]

#     # Get recommended restaurants
#     recommended_restaurants = restaurants.iloc[restaurant_indices]

#     # Refine recommendations based on extracted information and location
#     for _, restaurant in recommended_restaurants.iterrows():
#         if any(category in restaurant['categories'] for category in user_nouns) and any(location in restaurant['city'] for location in user_locations):
#             print(f"Refined recommendation: {restaurant['name']} based on type of food and location.")

#             # Get similar foods from the knowledge graph
#             additional_categories = set()
#             for user_noun in user_nouns:
#                 similar_foods = get_similar_foods(user_noun, knowledge_graph)
#                 additional_categories.update(similar_foods)

#             # Update the categories column with similar foods
#             updated_categories = ', '.join(set(restaurant['categories'].split(', ') + list(additional_categories)))
#             print(f"Updated Categories: {updated_categories}")

#             # Check restaurant availability based on current time
#             current_time = datetime.now().strftime("%H:%M")
#             if is_restaurant_open(restaurant['hours'], current_time):
#                 print(f"{restaurant['name']} is open right now!")
#             else:
#                 print(f"{restaurant['name']} is currently closed.")

# # Example prompt
# user_prompt = input("Enter your restaurant preference (e.g., I want Chinese in Brooklyn): ")

# # Get recommendations based on the user's input and availability, prioritizing location
# recommend_restaurants(user_prompt)
